In [1]:
import re
import csv
import json
import twint
import networkx as nx
from networkx.readwrite import json_graph
import requests
import os.path
from os import listdir
from os.path import isfile, join

In [2]:
def read_json_graph(filename):
    with open(filename) as f:
        js_graph = json.load(f)
    return json_graph.node_link_graph(js_graph)

In [3]:
# twint does not provide the support to get the usernames of the retweeters yet. Hence the function
def get_retweeters_list(username, tweet_id):
    # get the data of retweets
    r = requests.get('https://twitter.com/i/activity/retweeted_popup?id='+tweet_id)
    # use the grep in order to getch the retweeters
    text = r.text
    x = re.findall('div class=\\\\"account  js-actionable-user js-profile-popup-actionable \\\\" data-screen-name=\\\\"(.+?)\\\\" data-user-id=\\\\"', text)
    return x

In [4]:
# get the tweets that have been retweeted
def get_tweet_id(username):
    # open the tweets file of the user
    retweeted_tweets = []
    ids_list = []
    try:
        with open('StronglyConnectedUsers/'+username+'.csv') as csvfile:
            readCSV = csv.reader(csvfile, delimiter=',')
            for row in readCSV:
                if row[15] != '0' and row [0] != 'id':
                    retweeted_tweets.append(row[0])
    except:
        pass
    # return a list of tweet ID's
    return(retweeted_tweets)

In [5]:
subgrapsh_directory_path = "/Users/savanpatel/Desktop/sfsu/research/spamDetection/SDUTDPRev3/DataProcessing/SubGraphs/"
def get_subgraphs():
    # get all the subgraph list
    sub_graphs = [f for f in listdir(subgrapsh_directory_path) if isfile(join(subgrapsh_directory_path, f))]
    try:
        sub_graphs.remove(".DS_Store")
    except:
        pass
    return sub_graphs

In [6]:
sub_graphs = get_subgraphs()
print(len(sub_graphs))
complete_list_of_users = []
node_dict = {}
for item1 in sub_graphs:
    print(item1)
    # for each subgraph, get all the nodes and extract their top tweets
    G = nx.Graph()
    G = read_json_graph(subgrapsh_directory_path+item1)
    list_of_user = list(G.nodes)
    node_dict[item1] = list_of_user
    for item in list_of_user:
        complete_list_of_users.append(item)
print(node_dict)
print(len(complete_list_of_users))
with open('complete_list_of_users.txt', 'w') as f:  
    for user in complete_list_of_users:
        f.write('%s\n' % user)

8
15.0topic-SubGraph0.json
25.0topic-SubGraph0.json
23.0topic-SubGraph0.json
7.0topic-SubGraph0.json
14.0topic-SubGraph0.json
22.0topic-SubGraph0.json
3.0topic-SubGraph0.json
18.0topic-SubGraph0.json
{'15.0topic-SubGraph0.json': ['SimonFelip', 'pastdusk', 'THESUGARDAD1___', 'chefchaos1994', 'khayr_abu', 'Lobkeeeee123', 'emilyxstella', 'muyheex1086', 'SUGARMOMCINDY', 'iddo_iddo', 'PrideGiveaways', 'WiredINeSports', 'AltSugarmommy2', 'JBashire', 'Sugardadthomas', 'DeGiveawayKing1', 'adlanborzz420', 'TheSugarMommy2', 'TheSUGardad_13', 'trickylife', 'Comicone2'], '25.0topic-SubGraph0.json': ['FashoMoneyJohn', 'aviandeyez_', 'Lexi1DGirl', 'Morgan__ml', 'javonjourney', 'leslielo0ve', 'kvrinvojedv', 'princessC124', 'iitzy7', 'TooBasedChris', 'Only_OneLA', 'babybresshorty', 'zaytatted', 'zenxty', 'trevor_norris0', 'SayCrayton', 'Bluntreras', 'KameronBennett', 'iambromans', 'YoungKGhoo', 'jakecardiff401', '_djrocklee', 'kryptoNHIte', 'istrippymane', '_Alake', 'CraveFayyy', 'mikaelapeach', 'will

In [7]:
'''
After saving the users to acomplete_list_of_users.txt, run the tweet collection code from Pycharm.
Due to the underlying issues of jupyter, data collection code breaks while executing it here.
'''

'\nAfter saving the users to acomplete_list_of_users.txt, run the tweet collection code from Pycharm.\nDue to the underlying issues of jupyter, data collection code breaks while executing it here.\n'

In [8]:
# delete the old file and create a new blank one
if os.path.isfile("vector.csv"):
    print("file exists")
    os.remove("vector.csv")
open("vector.csv", 'a').close()

In [ ]:
with open('vector.csv', 'r+', newline='') as csvfile :
    vector = csv.writer(csvfile, delimiter=',')
    vector.writerow(['tweet_id']+list(node_dict.keys()))
    row1 = ['tweet_id']
    for graph_id in node_dict.keys():
        row1.append(graph_id)
    print(row1)
    buckets = [0] * len(node_dict.keys())
    for user in complete_list_of_users:
        # get list of tweet_id of retweeted tweets
        ids_of_retweeted_tweets = get_tweet_id(user)
        for id_tweet in ids_of_retweeted_tweets:
            # add a row to the csv file with the tweet_id
            row = [id_tweet]
            row.extend((buckets))
            # get the usernames of the retweeters
            retweeters = []
            retweeters = get_retweeters_list(user, id_tweet)
            # add tweet's oroginal poster to the list of retweeters to the vector
            retweeters.append(user)
            print(id_tweet)
            print(retweeters)
            # for each retweeter check if the retweeter is in the complete list of users
            for retweeter in retweeters:
                if retweeter in complete_list_of_users:
                    # if the retweeter exists in the complete list of users check which subgraph he/she belongs to
                    for sub_graph_users_key in node_dict.keys():
                        if retweeter in list(node_dict[sub_graph_users_key]):
                            print("\n"+id_tweet+" was retweeted by "+retweeter+" and is interested in topic "+sub_graph_users_key+"\n")
                            count = row[row1.index(sub_graph_users_key)]
                            count = count + 1
                            row[row1.index(sub_graph_users_key)] = count
            vector.writerow(row)

['tweet_id', '15.0topic-SubGraph0.json', '25.0topic-SubGraph0.json', '23.0topic-SubGraph0.json', '7.0topic-SubGraph0.json', '14.0topic-SubGraph0.json', '22.0topic-SubGraph0.json', '3.0topic-SubGraph0.json', '18.0topic-SubGraph0.json']
703613175900405760
['SimonFelip']

703613175900405760 was retweeted by SimonFelip and is interested in topic 15.0topic-SubGraph0.json

1111313855311863810
['husted_pope', 'KristanneJiskra', 'guywokebruh', 'THESUGARDAD1___']

1111313855311863810 was retweeted by THESUGARDAD1___ and is interested in topic 15.0topic-SubGraph0.json

1110718583204691974
['Izzybellea1', 'guywokebruh', 'enioxl', 'mcmaiola', 'SGF007', 'Camgirl065', 'peduzzi_thomas', 'THESUGARDAD1___']

1110718583204691974 was retweeted by THESUGARDAD1___ and is interested in topic 15.0topic-SubGraph0.json

1108227618187497472
['guywokebruh', 'THESUGARDAD1___', 'THESUGARDAD1___']

1108227618187497472 was retweeted by THESUGARDAD1___ and is interested in topic 15.0topic-SubGraph0.json


11082276181

1107709444027285504
['lupitowatson191', 'muyheex1086']

1107709444027285504 was retweeted by muyheex1086 and is interested in topic 15.0topic-SubGraph0.json

1107000503760756741
['sbdaehya', 'uwu_serena', 'Sblana1', 'Kittie49966645', 'smodfs', 'TheBlackBunny07', 'muyheex1086']

1107000503760756741 was retweeted by muyheex1086 and is interested in topic 15.0topic-SubGraph0.json

1106997487565443072
['Dziki1980', 'Kittie49966645', 'babyneeddaddy', 'TheBlackBunny07', 'muyheex1086']

1106997487565443072 was retweeted by muyheex1086 and is interested in topic 15.0topic-SubGraph0.json

1106879138168741889
['babyneeddaddy', 'JamesLe33475485', 'Sblana1', 'uwu_serena', 'jedonobx', 'AlbarranPerea', 'MandaMartinotti', 'Razel92657847', 'KieranRouse6', 'muyheex1086']

1106879138168741889 was retweeted by muyheex1086 and is interested in topic 15.0topic-SubGraph0.json

1106877622552879104
['kirkbymark', 'JamesLe33475485', 'Sblana1', 'uwu_serena', 'jedonobx', 'AlbarranPerea', 'MandaMartinotti', 'baby

1104533588089946120
['Swiftysports', 'itualfama', 'iddo_iddo', 'JennaLe96822673', 'temojin263', 'gnaneshwar504', 'hspnova', '01_jesuxx', 'dang58502410', 'Jangelica11', 'Kookiepuss1', 'SUGARMOMCINDY', 'steephanievane', 'EricaStover8', 'atlantis757', 'NeighborhoodFP', 'EddieMeintjes', 'velizar1990', 'itsoneon', 'leprincesow', 'Heather48580035', 'BruceDevlin10', 'Sibthjb', 'cnorth1979', 'BobBaratta99', 'SUGARMOMCINDY']

1104533588089946120 was retweeted by iddo_iddo and is interested in topic 15.0topic-SubGraph0.json


1104533588089946120 was retweeted by SUGARMOMCINDY and is interested in topic 15.0topic-SubGraph0.json


1104533588089946120 was retweeted by SUGARMOMCINDY and is interested in topic 15.0topic-SubGraph0.json

1104515360001155072
['sado744', 'MuzyGrant', 'leemccallon', 'Twittbabs17', 'Mr_Aren', 'getreal', 'Lobkeeeee123', 'DaddyDomX1', 'phoenixrisen970', 'oMystiiic', 'iddo_iddo', 'JennaLe96822673', 'itualfama', '_KendraLamar', 'gnaneshwar504', 'IngoingPanic22', 'XxJazminMarie

1116350878582222852
['qier_va', 'DikyEP', 'dianaaaaa029', 'fvcklonely', 'V_eye_cee', 'Dinnafrh', 'antoniadou_el', 'wdolfn', 'k1_NB156', 'yoonswit', '75SWARUPGHOSH', 'justcerii', 'messy_once', 'z331997', 'saputra_jeffry', 'Ereycaaa_', 'g_04ishan', 'bijjstangot7', 'nurartikaj', 'Quait16', 'moorejimmy1988', 'fitrianana01', 'tellmsp', 'electrichills_', 'Chozicrack', 'PrideGiveaways']

1116350878582222852 was retweeted by PrideGiveaways and is interested in topic 15.0topic-SubGraph0.json

1115873778041544704
['ShannFlann11', 'impulsfokus', 'pbgqts', 'Yagam1_1ight', 'PrideGiveaways', 'hellagorgeousme', 'PrideGiveaways']

1115873778041544704 was retweeted by PrideGiveaways and is interested in topic 15.0topic-SubGraph0.json


1115873778041544704 was retweeted by PrideGiveaways and is interested in topic 15.0topic-SubGraph0.json

1115690738703110144
['ShannFlann11', 'Locothebot', 'Yassine67707840', 'anrsyh_', 'leite_romeo', 'PrideGiveaways', 'delacroix111', 'lupitowatson191', '6_Yale', 'fajria

1110552526288547840
['Oneezybruh_32', 'lunarose121', 'franco_0515', 'guywokebruh', 'Selimadgzel15', 'LustingTeen', 'muscle_ginger', 'mon_ami92', 'BoxingGuy18', 'H41Lauren', 'beautyfly_oasis', 'Jovan88370592', 'jumeR6S', 'BambolaDiDolore', 'coupseukitten', 'pencilspencer', 'mallorypbaby28', 'Cyclone3366', 'Dave13255658', 'MickieElliott', 'phoenixrisen970', 'elstrup88', 'BrewcrewBarnes', 'Comicone2', 'BbyAmy3', 'Sugardadthomas']

1110552526288547840 was retweeted by Comicone2 and is interested in topic 15.0topic-SubGraph0.json


1110552526288547840 was retweeted by Sugardadthomas and is interested in topic 15.0topic-SubGraph0.json

1109813199728230401
['Fernand87706779', 'franco_0515', 'Selimadgzel15', 'NotBoios', 'QueenIsLyfe', 'Dave13255658', 'BrewcrewBarnes', 'Magick_Dream', 'OSOM_17', 'SandraTeeters1', 'RichardKrentcil', 'ATLienFalcon', 'ProslimZa', 'elstrup88', 'coupseukitten', 'RobertL1221', 'blkjp2011', 'OhYeahCountry', 'BbyAmy3', 'Isha_v0481', 'RN3ps', 'CroumerJr', 'EddieMeintjes

...

1108075731139981312
['LaOkieKat', 'bud_cann']

1108075731139981312 was retweeted by bud_cann and is interested in topic 23.0topic-SubGraph0.json

1108074746166411264
['taseymae', 'missy_zaccaro', 'bgdepuy', 'KNP2BP', 'RealityBoost', 'EdwardFallivene', 'star1capricorn', 'Wilks77731', 'marylene58', 'bud_cann', 'GingerCash777', 'RNcat50', 'SuzanneKnows', 'TMURPH88', 'squirellsRnutz', 'MichaelDadiego', 'WillWat14922206', 'smart_whit', 'o1d_dude', 'raybae689', 'DudshaDudsha1', 'pd_mspdcali', 'MagaNordic', 'museumof_man', 'GatesRobin', 'bud_cann']

1108074746166411264 was retweeted by bud_cann and is interested in topic 23.0topic-SubGraph0.json


1108074746166411264 was retweeted by bud_cann and is interested in topic 23.0topic-SubGraph0.json

1108071971416207360
['jeannemccoy17', 'Truthlikealion', 'KNP2BP', 'Truthbknown1111', 'kattalang', 'papamc01', 'RealityBoost', 'kflower1414', 'Epahlee', 'alpha_wolfen', 's_pboyd', 'AZ_IceB', 'LuhanskRepublic', 'Gav_Alfred9', 'abstract1dea', 'ultramanfly

1106931579031453696
['GrivicicMaryann', 'BrendaShoshanna', 'BrendaPeanci', 'KNP2BP', 'RARRRRR', 'smart_whit', 'dain50329875', 'realNick_777', 'OpalescentMoon', 'JimboGeology', 'LindaForAmerica', 'brucehudson7', 'yojudenz', 'alpipkin', 'Lyn1350', 'Dougs1978', 'camille_tine', 'KenGrimes9', 'AsilanaQAnon', 'chbstone2', 'MslillieMaga', 'phsdad', 'Lexa_Merica', 'Yolanda53311253', 'mawmy', 'bud_cann']

1106931579031453696 was retweeted by bud_cann and is interested in topic 23.0topic-SubGraph0.json

1106762521698983936
['GrivicicMaryann', 'FredricDelmais', 'KNP2BP', 'donaldbroom', 'paru51a', 'MistyDa84100630', 'realNick_777', 'powerglobalus', 'DeplorableBugsy', 'NealWCopeland2', 'avibebert', 'JimScotty', 'AdamsWfa551', 'CaroCrt', 'accident', 'TruthEqsJustice', 'Lexa_Merica', 'Melissa24705356', 'CarolynKleinpe1', 'jeannemccoy17', 'pvtharoldmoon', 'ScribbledPages1', 'JTeisan', 'JuliaFromQueens', 'cashflow28963', 'bud_cann']

1106762521698983936 was retweeted by bud_cann and is interested in to

1106215970396225536
['patopines', 'Wilks77731', 'cisppetta', 'SaveAslave', 'KNP2BP', 'jhc3737', 'RichardPaquett2', 'lrnewton1', 'Def18436572', 'AlwaysAMarine70', 'bud_cann', 'lardogthemarine', 'All4hoodRandy', 'jbryant710', 'CHauert', 'Oma8612', 'hansgribble', 'Connie_M_Rice', 'Joey88485612', 'Missing_Winnie', 'Dogs_Daze', 'smart_whit', 'piper_low', '2Thedogpound', 'Floridaartist1', 'bud_cann']

1106215970396225536 was retweeted by bud_cann and is interested in topic 23.0topic-SubGraph0.json


1106215970396225536 was retweeted by bud_cann and is interested in topic 23.0topic-SubGraph0.json

1106211828642734082
['smart_whit', 'Stateline69J', 'lynnmccain55', 'hrothenb', 'urokimtwo', 'Dave13593715', 'IMISTHEBOWLBROS', 'IamcldPatricia', 'bucketoftea', 'LisaSmith4680', 'patriotscloset', 'MurrayDgmurray', 'PatriotPennsy', 'shawnssi', 'Davidhu46883012', 'kkbrando', 'Watchman33Eze', 'deanbc1', 'TheMikeMind', 'Nth_Dimensions', 'SamCantrell14', 'goober01013', 'Dougs1978', 'LindaForAmerica', 'SAn

1105496325229961216
['PhillipLaird', 'marburell', 'CorinnaBohme', 'doddrose', 'infowarsholland', 'smart_whit', 'az_sweetpea', 'ROHLL5', 'FN92', 'FreeTho58307560', 'Wrileygirl1961', 'sherrynron', 'JeffG701', 'panganashe', 'LisaSmith4680', 'KNP2BP', 'meWooster', 'stumpy1258', 'CZ4ever60', 'howardmood449', 'PeaceToYouAmen', 'ReneeCarrollAZ', '19soulmate77', 'HHinKL', 'pbprecious7', 'bud_cann']

1105496325229961216 was retweeted by bud_cann and is interested in topic 23.0topic-SubGraph0.json

1105493535287963649
['Treya108', 'Tbig48', 'Carrie_Kelly17', 'AllenEllis14', 'foxybubba18', 'PhillipLaird', 'CorinnaBohme', 'infowarsholland', 'z_chrissie', 'smartvalueinfo', 'smart_whit', 'ROHLL5', 'FreeTho58307560', 'MickyFin', 'sherrynron', 'GrivicicMaryann', 'Carver926', 'TillmanSensei', 'PeterLe30125667', 'ScribbledPages1', 'IrisArc91599747', 'JaKay539', 'PonsFaciaBella', 'goldwaterkid65', 'Paulr19417777Sr', 'bud_cann']

1105493535287963649 was retweeted by bud_cann and is interested in topic 23.

1104840377339527168
['StadiumHopper', 'italianmystery', 'maharru', 'ChucksWife1973', 'georgatos_t', 'Jbrock130', 'pwaldrop33', 'IvanNetwork', 'MarkMccomack', 'elizabehsotner', 'Gastein', 'mcmahen_t', 'ANCIENTENGRAVIN', 'WilliamBurt9', 'MaureenMRD1024', 'bigdirtyhairgm1', 'MeJeffBond', 'jonahogan', 'NYMesherman', 'RNcat50', 'bobbrandt362', 'Berry91972268', 'FakeSabresGM', 'GrivicicMaryann', 'Stubby0207', 'bud_cann']

1104840377339527168 was retweeted by bud_cann and is interested in topic 23.0topic-SubGraph0.json

1104836439177551872
['GoGreen33333333', 'mglessman', 'ANCIENTENGRAVIN', 'daravi1316', 'NikkythaBee', 'GrivicicMaryann', 'Cathir472', 'mobileal2017', 'vandezoro', 'Oma8612', 'kikilauridsen', 'Stargaz98500427', 'JoeREstrada', 'loves_nra', 'ElizabethCarron', 'Vicky4Trump', 'CarlisleDavey', 'SingarRTO', 'SwissBetz', 'BrushOn2017', 'HeartsNJunk', 'roseoshar7', 'mikewilson6785', 'CJUSTICETruth41', 'PamCouch87', 'bud_cann']

1104836439177551872 was retweeted by bud_cann and is intere